# Solução do Execicio 2

Import e leitura

In [1]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import KFold, RandomizedSearchCV
from sklearn.linear_model import LinearRegression, Ridge
from sklearn.metrics import mean_squared_error
np.set_printoptions(precision=3)

In [2]:
def sembusca(est):
    kf = KFold()
    soma = 0.0
    for train_index, test_index in kf.split(X,y):
        X_train, X_test = X[train_index,:], X[test_index,:]
        y_train, y_test = y[train_index], y[test_index]
        modelo = est.fit(X_train,y_train)
        yout = modelo.predict(X_test)
        soma += mean_squared_error(y_test,yout,squared=False)

    res = soma/5
    return res

In [3]:
tabela = {}
dat = pd.read_csv('https://archive.ics.uci.edu/ml/machine-learning-databases/00514/Bias_correction_ucl.csv')
print(dat.shape)
dat = dat.dropna()
print(dat.shape)
dat

(7752, 25)
(7588, 25)


station        Date  Present_Tmax  Present_Tmin  LDAPS_RHmin  \
0         1.0  2013-06-30          28.7          21.4    58.255688   
1         2.0  2013-06-30          31.9          21.6    52.263397   
2         3.0  2013-06-30          31.6          23.3    48.690479   
3         4.0  2013-06-30          32.0          23.4    58.239788   
4         5.0  2013-06-30          31.4          21.9    56.174095   
...       ...         ...           ...           ...          ...   
7745     21.0  2017-08-30          23.1          17.8    24.688997   
7746     22.0  2017-08-30          22.5          17.4    30.094858   
7747     23.0  2017-08-30          23.3          17.1    26.741310   
7748     24.0  2017-08-30          23.3          17.7    24.040634   
7749     25.0  2017-08-30          23.2          17.4    22.933014   

      LDAPS_RHmax  LDAPS_Tmax_lapse  LDAPS_Tmin_lapse  LDAPS_WS    LDAPS_LH  \
0       91.116364         28.074101         23.006936  6.818887   69.451805   
1       90.604721         29.850689         24.035009  5.691890   51.937448   
2       83.973587         30.091292         24.565633  6.138224   20.573050   
3       96.483688         29.704629         23.326177  5.650050   65.727144   
4       90.155128         29.113934         23.486480  5.735004  107.965535   
...           ...               ...               ...       ...         ...   
7745    78.261383         27.812697         18.303014  6.603253    9.614074   
7746    83.690018         26.704905         17.814038  5.768083   82.146707   
7747    78.869858         26.352081         18.775678  6.148918   72.058294   
7748    77.294975         27.010193         18.733519  6.542819   47.241457   
7749    77.243744         27.939516         18.522965  7.289264    9.090034   

      ...  LDAPS_PPT2  LDAPS_PPT3  LDAPS_PPT4      lat      lon       DEM  \
0     ...         0.0         0.0         0.0  37.6046  126.991  212.3350   
1     ...         0.0         0.0         0.0  37.6046  127.032   44.7624   
2     ...         0.0         0.0         0.0  37.5776  127.058   33.3068   
3     ...         0.0         0.0         0.0  37.6450  127.022   45.7160   
4     ...         0.0         0.0         0.0  37.5507  127.135   35.0380   
...   ...         ...         ...         ...      ...      ...       ...   
7745  ...         0.0         0.0         0.0  37.5507  127.040   26.2980   
7746  ...         0.0         0.0         0.0  37.5102  127.086   21.9668   
7747  ...         0.0         0.0         0.0  37.5372  126.891   15.5876   
7748  ...         0.0         0.0         0.0  37.5237  126.909   17.2956   
7749  ...         0.0         0.0         0.0  37.5237  126.970   19.5844   

       Slope  Solar radiation  Next_Tmax  Next_Tmin  
0     2.7850      5992.895996       29.1       21.2  
1     0.5141      5869.312500       30.5       22.5  
2     0.2661      5863.555664       31.1       23.9  
3     2.5348      5856.964844       31.7       24.3  
4     0.5055      5859.552246       31.2       22.5  
...      ...              ...        ...        ...  
7745  0.5721      4456.024414       27.6       17.7  
7746  0.1332      4441.803711       28.0       17.1  
7747  0.1554      4443.313965       28.3       18.1  
7748  0.2223      4438.373535       28.6       18.8  
7749  0.2713      4451.345215       27.8       17.4  

[7588 rows x 25 columns]

In [4]:
y = dat['Next_Tmax'].to_numpy()
X = dat.drop(['Next_Tmin','Date'], axis=1).to_numpy()

## Scaling e centering

Eu nao vejo uma boa razao para NAO usar sempre (ou quase sempre) o centering e scaling.

In [5]:
X = StandardScaler().fit_transform(X)

## Regressão linear

In [6]:
res = sembusca(LinearRegression())
    
tabela['reglinear'] = (res,res)
print('RMSE: {:.3} Default:{:.3}'.format(res,res))

RMSE: 4.38e-15 Default:4.38e-15


## Regressão linear com regularização L2

In [7]:
import random
random.seed(42)
melhor = np.Inf
for volta in range(10):
    alfa = 10**random.uniform(-3.0,3.0)
    res = sembusca(Ridge(alpha=alfa))
    
    if res < melhor:
        melhor = res

z = sembusca(Ridge())        
        
tabela['reglinearL2'] = (melhor,z)
print('RMSE: {:.3} Default:{:.3}'.format(melhor,z))

RMSE: 1.72e-06 Default:0.00121


## Regressao linear com L1

Vamos usar o [RandomizedSearchCV](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.RandomizedSearchCV.html#sklearn.model_selection.RandomizedSearchCV) em vez de fazer o loop diretamente

Este codigo é meio chato pois a distribuiçao de probabilidade do parametro alpha é uniforme no exponente. O que significa que a distribioçao do parametro é [loguniform](https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.loguniform.html#scipy.stats.loguniform). Neste caso voce da o menor valor e o maior valor (como se fosse uma distribuiçao uniforme). 

In [8]:
from sklearn.model_selection import RandomizedSearchCV
from sklearn.linear_model import Lasso
from scipy.stats import loguniform
from math import sqrt

In [9]:
est= Lasso()

pardistr = dict(alpha = loguniform(10**(-3.0),10**3.0))

rcv = RandomizedSearchCV(est,param_distributions=pardistr,n_iter=10,cv=5,scoring = 'neg_root_mean_squared_error', 
                         random_state=42)
res = rcv.fit(X,y)

melhor = -res.best_score_

z = sembusca(est)      

tabela['reglinearL1'] = (melhor,z)
print('RMSE: {:.3} Default:{:.3}'.format(melhor,z))

RMSE: 0.00227 Default:1.02


## SVMLinear

In [10]:
from sklearn.svm import LinearSVR

est = LinearSVR()

pardistr = dict(C = loguniform(2**(-5.0),2**15.0), epsilon=[0.1,0.3])

rcv = RandomizedSearchCV(est,param_distributions=pardistr,n_iter=10,cv=5,scoring = 'neg_root_mean_squared_error', 
                         random_state=42)
res = rcv.fit(X,y)

melhor = -res.best_score_

z = sembusca(est)      

tabela['linearSVM'] = (melhor,z)
print('RMSE: {:.3} Default:{:.3}'.format(melhor,z))


RMSE: 0.1 Default:6.23e-12


## SVM

In [11]:
from sklearn.svm import SVR

est = SVR(kernel='rbf')

pardistr = dict(C = loguniform(2**(-5.0),2**15.0), epsilon=[0.1,0.3],gamma=loguniform(2**(-9),2**3))

rcv = RandomizedSearchCV(est,param_distributions=pardistr,n_iter=10,cv=5,scoring = 'neg_root_mean_squared_error', 
                         random_state=42)
res = rcv.fit(X,y)

melhor = -res.best_score_

z = sembusca(est)      

tabela['SVM'] = (melhor,z)
print('RMSE: {:.3} Default:{:.3}'.format(melhor,z))


RMSE: 0.122 Default:0.558


## KNN

In [12]:
from sklearn.neighbors import KNeighborsRegressor
from scipy.stats import randint

est = KNeighborsRegressor()

pardistr = dict(n_neighbors = randint(1,1000))

rcv = RandomizedSearchCV(est,param_distributions=pardistr,n_iter=10,cv=5,scoring = 'neg_root_mean_squared_error', 
                         random_state=42)
res = rcv.fit(X,y)

melhor = -res.best_score_

z = sembusca(est)      

tabela['KNN'] = (melhor,z)
print('RMSE: {:.3} Default:{:.3}'.format(melhor,z))


RMSE: 1.4 Default:1.42


## MLP

In [13]:
from sklearn.neural_network import MLPRegressor
from sklearn.model_selection import GridSearchCV

est = MLPRegressor(max_iter=400,random_state=42)

pardistr = dict(hidden_layer_sizes = list(map(lambda x: (x,), range(5,21,3))))

rcv = GridSearchCV(est,param_grid=pardistr,cv=5,scoring = 'neg_root_mean_squared_error')

res = rcv.fit(X,y)

melhor = -res.best_score_

z = sembusca(est)      

tabela['MLP'] = (melhor,z)
print('RMSE: {:.3} Default:{:.3}'.format(melhor,z))


/opt/miniconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (400) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/opt/miniconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (400) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/opt/miniconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (400) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/opt/miniconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (400) reached and the optimization hasn't converged yet.
  % self.max_iter, 

RMSE: 0.18 Default:0.358


/opt/miniconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (400) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)


## Arvore de decisão

In [14]:
from sklearn.tree import DecisionTreeRegressor
from scipy.stats import uniform

est = DecisionTreeRegressor()

pardistr = dict(ccp_alpha = uniform(0,0.04))

rcv = RandomizedSearchCV(est,param_distributions=pardistr,n_iter=10,cv=5,scoring = 'neg_root_mean_squared_error', 
                         random_state=42)
res = rcv.fit(X,y)

melhor = -res.best_score_

z = sembusca(est)      

tabela['Arvore'] = (melhor,z)
print('RMSE: {:.3} Default:{:.3}'.format(melhor,z))


RMSE: 0.177 Default:0.0296


## Random Forest

In [15]:
from sklearn.ensemble import RandomForestRegressor

est = RandomForestRegressor(random_state=42)

pardistr = dict(n_estimators=[10,100,1000],max_features=[5, 10, 22])

rcv = GridSearchCV(est,param_grid=pardistr,cv=5,scoring = 'neg_root_mean_squared_error')

res = rcv.fit(X,y)

melhor = -res.best_score_

z = sembusca(est)      

tabela['RF'] = (melhor,z)
print('RMSE: {:.3} Default:{:.3}'.format(melhor,z))


RMSE: 0.03 Default:0.0281


## GBM

In [17]:
from sklearn.ensemble import GradientBoostingRegressor

est = GradientBoostingRegressor(random_state=42
                               )
pardistr = dict(n_estimators=randint(5,100), learning_rate=uniform(0.01,0.3),max_depth=[2,3])

rcv = RandomizedSearchCV(est,param_distributions=pardistr,n_iter=10,cv=5,scoring = 'neg_root_mean_squared_error', 
                         random_state=42)
res = rcv.fit(X,y)

melhor = -res.best_score_

z = sembusca(est)      

tabela['GBM'] = (melhor,z)
print('RMSE: {:.3} Default:{:.3}'.format(melhor,z))




RMSE: 0.0663 Default:0.0348


In [18]:
df = pd.DataFrame(columns=["Algoritmo","RMSE","Default"])
i=0
for alg,x in tabela.items():
    try:
        df.loc[i] = alg,x[0],x[1]
    except:
        df.loc[i] = alg,x,1000.0
    i+=1


In [19]:
pd.set_option('precision', 3)
print(df)

     Algoritmo       RMSE    Default
0    reglinear  4.378e-15  4.378e-15
1  reglinearL2  1.718e-06  1.215e-03
2  reglinearL1  2.273e-03  1.019e+00
3    linearSVM  9.997e-02  6.229e-12
4          SVM  1.224e-01  5.583e-01
5          KNN  1.399e+00  1.415e+00
6          MLP  1.797e-01  3.577e-01
7       Arvore  1.771e-01  2.956e-02
8           RF  3.001e-02  2.812e-02
9          GBM  6.634e-02  3.480e-02
